# Introduction

## Définitions

La **matrice de confusion** est un tableau où on décompte les valeurs réelle O et prédites S pour chaque observation du jeu de données dans un problème de classification. Par sa conception, on peut valider rapidement le nombre d'observations où la prédiction est égale à la valeur réelle sur la diagonale de la matrice. Par convention, on place les valeurs prédites à la verticale et les valeurs observées à l'horizontale. Lorsque le nombre de modalités de la variable prédite est de deux, on a un problème de classification binaire et on obtient alors le décompte des vrais positifs, faux positifs, faux négatifs et vrais négatifs.

La **précision** correspont à la proportion d'observations où la prédiction et la valeur réelle est dans une même classe par rapport au nombre d'observations où la prédiction est dans cette classe

$$ \text{Précision}_c =  \frac{\sum_{i=1}^N 1_{s_i=c}1_{o_i=c}}{\sum_{i=1}^N 1_{s_i=c}}$$

Le **rappel** correspond à la proportions d'observations où la prédiction est dans une classe par rapport au nombre d'observations où la valeur réelle est dans cette classe.

$$ \text{Rappel}_c =  \frac{\sum_{i=1}^N 1_{s_i=c}}{\sum_{i=1}^N 1_{o_i=c}}$$

## Librairies utilisées

Le project actuel est programmé dans le langage Python 3, et ce rapport est produit à l'aide de Jupyter Notebook. Seule les librairie standard `numpy` et `math` est utilisée, les autres ont été développées dans le cadre de ce projet.

In [1]:
# Librairies standard
import numpy as np
import math
# Librairies développées par l'étudiant
import load_datasets as ld
import BayesNaif
import Knn
import metrics

## Jeux de données

Ce projet utilise 3 jeux de données: [Iris](https://archive.ics.uci.edu/ml/datasets/Iris), [MONKS](https://archive.ics.uci.edu/ml/datasets/MONK's+Problems) et [Congressional Voting Records Dataset](https://archive.ics.uci.edu/ml/datasets/Congressional+Voting+Records)

# Algorithme des k plus proches voisins (kNN)

Dans cette section, on présente les résultats obtenus pour l'algorithme des k plus proches voisins. Ce n'est pas un algorithme d'apprentissage à proprement parler, car il n'y a aucun modèle d'entrainé. On prédit la classe d'un nouvel élément en recherchant les k plus proches voisins selon une métrique choisie. Dans notre cas, nous utiliserons la distance de Minkowski, qui est une généralisation de la distance euclidienne et de la distance de Manhattan à l'aide d'un paramètre p. 

$${\displaystyle D\left(X,Y\right)=\left(\sum _{i=1}^{N}|o_{i}-s_{i}|^{p}\right)^{1/p}}$$

On peut ainsi itérer sur différentes valeurs de ce paramètre pour trouver la mesure la plus adaptée au problème, tout en réutilisant la même fonction. Cette métrique s'utilise aurant pour des domaines de valeurs continus que discrets.

## Pseudocode

- Entrainement

```
Copier le jeu d'entrainement et les étiquettes d'entrainement dans la mémoire du modèle
```

- Prédiction Knn
```
Pour une observation x_i:
    Entrainement <- Vrai si on fait le premier entrainement
    T = copie jeu d'entrainement
    L = copie des étiquettes d'entrainement
    K = tableau de paires (point, distance) de longueur k
    Si Entrainement:
        Enlever x de T et l'étiquette de x_i de L
    Pour chaque observation t_j, j=[1,k]) de T:
        d(x_i,t_i) = distance de Minkowski entre x_i et t_j
        K[j] <- (t_i,d(x_i,t_j)) 
    Pour chaque observation t_j, j=[k+1,N-1] de T:
        d(x,t_i) = distance de Minkowski entre x_i et t_j
        d_max <- distance maximum dans K
        pos_d_max <- position de d_max dans K
        Si d(x_i,t_j) < d_max
            Remplacer le point K[pos_d_max] par (t_j,d(x,t_j))
    s <- mode des valeurs des étiquettes des points dans K
    retourner s
```

- Test

```
Pour chaque observation x_i, i=1,N:
    S_i <- Prédiction(x_i)
M <- matrice de confusion avec les étiquettes d'entrainement et les étiquettes S
Calculer les métriques depuis M
```

- Validation croisée

```
K <- Valeurs à tester pour le nombre de voisins
Pour un jeu d'entrainement x
Permuter aléatoirement les nombre de 1 à N
Diviser la permutation en L groupes approximativement égaux
Pour l dans L:
    

Pour k dans K:
    Pour l dans L:
        Effectuer l'entrainement avec k voisins, x[sans l] comme jeu d'entrainement 
        Effectuer le test avec x[l] comme jeu de validation
        Calculer l'exactitude
    Prendre la moyenne des exactitudes
Prendre le k avec la meilleur exactitude moyenne
```

## Iris Dataset

On utilise 70% des données pour le jeu d'entrainement et 30% des données pour le jeu de test

In [2]:
train1, train_labels1, test1, test_labels1 = ld.load_iris_dataset(train_ratio = 0.7)

On crée un premier modèle afin d'identifier la meilleure valeur de k

In [3]:
findbest_Knn = Knn.Knn()
meilleur_k = findbest_Knn.set_best_k(train1, train_labels1, nb_split=5, k_potentiel=range(2,12))

/home/francois/gitea/ift7025-projet/Code/metrics.py:40: RuntimeWarning: invalid value encountered in double_scalars
  precision.append(cm[label_num,label_num] / sum(cm[:,label_num]))


Le meilleur k est: 9


On crée maintenant un nouveau modèle où on initialise la valeur de K avec celle trouvée précédemment

In [4]:
myKnn = Knn.Knn(meilleur_k)

On effectue l'entrainement du modèle (la copie du jeu d'entrainement et des étiquettes en mémoire) et on obtient les mesures de validation pour ce jeu d'entraînement. Les valeurs des métriques de précision et de rappel sont calculées pour chacune des étiquettes.

In [5]:
training_iris_knn = myKnn.train(train1, train_labels1)

Matrice de confusion:
[[35.  0.  0.]
 [ 0. 32.  1.]
 [ 0.  3. 34.]]

Accuracy:
0.9619047619047619

Precision:
[1.0, 0.9142857142857143, 0.9714285714285714]

Recall
[1.0, 0.9696969696969697, 0.918918918918919]


On effectue maintenant le test avec l'échantillon de test

In [6]:
test_iris_knn = myKnn.test(test1, test_labels1)

Matrice de confusion:
[[15.  0.  0.]
 [ 0. 16.  1.]
 [ 0.  1. 12.]]

Accuracy:
0.9555555555555556

Precision:
[1.0, 0.9411764705882353, 0.9230769230769231]

Recall
[1.0, 0.9411764705882353, 0.9230769230769231]


## Monks Dataset

In [7]:
train2, train_labels2, test2, test_labels2 = ld.load_monks_dataset(1)
train3, train_labels3, test3, test_labels3 = ld.load_monks_dataset(2)
train4, train_labels4, test4, test_labels4 = ld.load_monks_dataset(3)

### Premier sous-ensemble

- On identifie la meilleure valeur de k

In [8]:
findbest_Knn = Knn.Knn()
meilleur_k = findbest_Knn.set_best_k(train2, train_labels2, nb_split=5, k_potentiel=range(2,12))

Le meilleur k est: 4


In [9]:
myKnn2 = Knn.Knn(meilleur_k)

- On effectue l'entrainement du modèle

In [10]:
training_monks1_knn = myKnn2.train(train2, train_labels2)

Matrice de confusion:
[[32. 30.]
 [16. 46.]]

Accuracy:
0.6290322580645161

Precision:
[0.6666666666666666, 0.6052631578947368]

Recall
[0.5161290322580645, 0.7419354838709677]


- On effectue maintenant le test avec l'échantillon de test

In [11]:
test_monks1_knn = myKnn2.test(test2, test_labels2)

Matrice de confusion:
[[129.  87.]
 [ 38. 178.]]

Accuracy:
0.7106481481481481

Precision:
[0.7724550898203593, 0.6716981132075471]

Recall
[0.5972222222222222, 0.8240740740740741]


### Second sous-ensemble

- On identifie la meilleure valeur de k

In [12]:
findbest_Knn = Knn.Knn()
meilleur_k = findbest_Knn.set_best_k(train3, train_labels3, nb_split=5, k_potentiel=range(2,12))

Le meilleur k est: 5


In [13]:
myKnn3 = Knn.Knn(meilleur_k)

- On effectue l'entrainement du modèle

In [14]:
training_monks2_knn = myKnn3.train(train3, train_labels3)

Matrice de confusion:
[[104.   1.]
 [ 63.   1.]]

Accuracy:
0.621301775147929

Precision:
[0.6227544910179641, 0.5]

Recall
[0.9904761904761905, 0.015625]


- On effectue maintenant le test avec l'échantillon de test

In [15]:
test_monks2_knn = myKnn3.test(test3, test_labels3)

Matrice de confusion:
[[286.   4.]
 [133.   9.]]

Accuracy:
0.6828703703703703

Precision:
[0.6825775656324582, 0.6923076923076923]

Recall
[0.9862068965517241, 0.06338028169014084]


### Troisième sous-ensemble

- On identifie la meilleure valeur de k

In [16]:
findbest_Knn = Knn.Knn()
meilleur_k = findbest_Knn.set_best_k(train4, train_labels4, nb_split=5, k_potentiel=range(2,12))

Le meilleur k est: 5


In [17]:
myKnn4 = Knn.Knn(meilleur_k)

- On effectue l'entrainement du modèle

In [18]:
training_monks3_knn = myKnn4.train(train4, train_labels4)

Matrice de confusion:
[[27. 35.]
 [ 1. 59.]]

Accuracy:
0.7049180327868853

Precision:
[0.9642857142857143, 0.6276595744680851]

Recall
[0.43548387096774194, 0.9833333333333333]


- On effectue maintenant le test avec l'échantillon de test

In [19]:
test_monks3_knn = myKnn4.test(test4, test_labels4)

Matrice de confusion:
[[ 99. 105.]
 [  8. 220.]]

Accuracy:
0.7384259259259259

Precision:
[0.9252336448598131, 0.676923076923077]

Recall
[0.4852941176470588, 0.9649122807017544]


## Congressional Voting Records Dataset

In [20]:
train5, train_labels5, test5, test_labels5 = ld.load_congressional_dataset(0.7)

- On identifie la meilleure valeur de k

In [21]:
findbest_Knn = Knn.Knn()
meilleur_k = findbest_Knn.set_best_k(train5, train_labels5, nb_split=5, k_potentiel=range(2,12))

Le meilleur k est: 9


In [22]:
myKnn5 = Knn.Knn(meilleur_k)

- On effectue l'entrainement du modèle

In [23]:
training_congres_knn = myKnn5.train(train5, train_labels5)

Matrice de confusion:
[[ 76.  33.]
 [ 15. 180.]]

Accuracy:
0.8421052631578947

Precision:
[0.8351648351648352, 0.8450704225352113]

Recall
[0.6972477064220184, 0.9230769230769231]


- On effectue maintenant le test avec l'échantillon de test

In [24]:
test_congres_knn = myKnn5.test(test5, test_labels5)

Matrice de confusion:
[[42. 17.]
 [ 6. 66.]]

Accuracy:
0.8244274809160306

Precision:
[0.875, 0.7951807228915663]

Recall
[0.711864406779661, 0.9166666666666666]


# Algorithme Naive Bayes